In [2]:
# импорт необходимых библиотек

from typing import Union
from tqdm import tqdm

import pandas as pd
import numpy as np
import plotly.express as px
import matplotlib.pyplot as plt
import seaborn as sns

from scipy import stats
from statsmodels.stats.meta_analysis import effectsize_smd
from statsmodels.stats import proportion
from statsmodels.stats.power import tt_ind_solve_power
from statsmodels.stats.power import zt_ind_solve_power

import warnings
warnings.filterwarnings('ignore')
warnings.warn('DelftStack')
warnings.warn('Do not show this message')


Тестовая задача на АБ тесты.

Проанализируйте результаты эксперимента и напишите свои рекомендации менеджеру.

Mobile Games AB Testing with Cookie Cats


### Подготовка данных
- загрузка
- проверка 
- обработка и очистка

In [3]:
df = pd.read_csv('gb_sem_9_hw.csv')
df

userid  version  sum_gamerounds  retention_1  retention_7
0          116  gate_30               3        False        False
1          337  gate_30              38         True        False
2          377  gate_40             165         True        False
3          483  gate_40               1        False        False
4          488  gate_40             179         True         True
...        ...      ...             ...          ...          ...
90184  9999441  gate_40              97         True        False
90185  9999479  gate_40              30        False        False
90186  9999710  gate_30              28         True        False
90187  9999768  gate_40              51         True        False
90188  9999861  gate_40              16        False        False

[90189 rows x 5 columns]

In [4]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 90189 entries, 0 to 90188
Data columns (total 5 columns):
 #   Column          Non-Null Count  Dtype 
---  ------          --------------  ----- 
 0   userid          90189 non-null  int64 
 1   version         90189 non-null  object
 2   sum_gamerounds  90189 non-null  int64 
 3   retention_1     90189 non-null  bool  
 4   retention_7     90189 non-null  bool  
dtypes: bool(2), int64(2), object(1)
memory usage: 2.2+ MB


In [5]:
df.shape

(90189, 5)

In [6]:
df.describe()

userid  sum_gamerounds
count  9.018900e+04    90189.000000
mean   4.998412e+06       51.872457
std    2.883286e+06      195.050858
min    1.160000e+02        0.000000
25%    2.512230e+06        5.000000
50%    4.995815e+06       16.000000
75%    7.496452e+06       51.000000
max    9.999861e+06    49854.000000

In [7]:
df.isna().sum()

userid            0
version           0
sum_gamerounds    0
retention_1       0
retention_7       0
dtype: int64

In [8]:
df.version.replace({'gate_30': 0, 'gate_40': 1}, inplace=True)
df

userid  version  sum_gamerounds  retention_1  retention_7
0          116        0               3        False        False
1          337        0              38         True        False
2          377        1             165         True        False
3          483        1               1        False        False
4          488        1             179         True         True
...        ...      ...             ...          ...          ...
90184  9999441        1              97         True        False
90185  9999479        1              30        False        False
90186  9999710        0              28         True        False
90187  9999768        1              51         True        False
90188  9999861        1              16        False        False

[90189 rows x 5 columns]

### Начинаем делать аналитику

#### Необходимые функции

In [9]:
def continious_result(control: pd.DataFrame,
                      treatment: pd.DataFrame,
                      column: str,
                      n_iters: int = 10_000) -> pd.DataFrame:
    # Статистика по выборкам
    size = control.loc[:, column].shape[0]

    control_mean = control.loc[:, column].mean()
    treatment_mean = treatment.loc[:, column].mean()

    control_std = control.loc[:, column].std(ddof=1)
    treatment_std = treatment.loc[:, column].std(ddof=1)

    # Бутсрап
    booted_diff = []
    for _ in tqdm(range(n_iters)):
        control_sample = control.loc[:, column].sample(
            n=size, replace=True).values
        treatment_sample = treatment.loc[:, column].sample(
            n=size, replace=True).values
        booted_diff.append(np.mean(control_sample - treatment_sample))

    # Считаем статистику после бустрапа
    md_ci, std_ci = np.mean(booted_diff), np.std(booted_diff, ddof=1)
    left_ci, right_ci = np.percentile(booted_diff, [2.5, 97.5])
    p_value_ci = 2 * (1 - stats.norm.cdf(np.abs(md_ci / std_ci)))

    # Считаем мощность эксперимента
    effect_size, _ = effectsize_smd(mean1=treatment_mean, sd1=treatment_std, nobs1=size,
                                    mean2=control_mean, sd2=control_std, nobs2=size)
    power = tt_ind_solve_power(effect_size=effect_size,
                               nobs1=size,
                               alpha=.05,
                               power=None,
                               ratio=1)
    # Формируем отчёт
    result = pd.DataFrame({'effect_size': effect_size,
                           'alpha': p_value_ci,
                           'beta': (1-power),
                           'CI': f'[{np.round(left_ci, 3)}, {np.round(right_ci, 3)}]',
                           'difference': md_ci, },
                          index=[column])
    return result


In [10]:

def proportion_result(control: pd.DataFrame,
                      treatment: pd.DataFrame,
                      column: str,
                      n_iters: int = 10_000) -> pd.DataFrame:
    # Вероятность событий
    size = control.loc[:, column].shape[0]
    prop_control = control.loc[:, column].sum() / size
    prop_treatment = treatment.loc[:, column].sum() / size

    # Бутсрап
    booted_diff = []
    for _ in tqdm(range(n_iters)):
        control_sample = stats.bernoulli.rvs(p=prop_control, size=size)
        treatment_sample = stats.bernoulli.rvs(p=prop_treatment, size=size)
        booted_diff.append(np.mean(control_sample - treatment_sample))

    # Считаем статистику после бустрапа
    md_ci, std_ci = np.mean(booted_diff), np.std(booted_diff, ddof=1)
    left_ci, right_ci = np.percentile(booted_diff, [2.5, 97.5])
    p_value_ci = 2 * (1 - stats.norm.cdf(np.abs(md_ci / std_ci)))

    # Считаем мощность эксперимента
    effect_size = proportion.proportion_effectsize(
        prop_control, prop_treatment)

    power = zt_ind_solve_power(effect_size=effect_size,
                               nobs1=size,
                               alpha=.05,
                               power=None,
                               ratio=1)
    # Формируем отчёт
    result = pd.DataFrame({'effect_size': effect_size,
                           'alpha': p_value_ci,
                           'beta': (1-power),
                           'CI': f'[{np.round(left_ci, 3)}, {np.round(right_ci, 3)}]',
                           'difference': md_ci, },
                          index=[column])
    return result


#### Определимся с целевыми показателями

In [13]:
control = df[df.version == 0].copy(deep=True)
treatment = df[df.version == 1].copy(deep=True)
control.shape, treatment.shape


((44700, 5), (45489, 5))

### Метрика **sum_gamerounds**

In [14]:
fig = px.histogram(df,
                   x='sum_gamerounds',
                   color='version',
                   title='Среднее распределение прохождения уровней в игре',
                   marginal='box',
                   nbins=300,
                   barmode='overlay')

fig.show()


Очевидно, что в данных есть выброс. При среднем и медианном значении в 50 и 200 уровней, один пользователь прошел почти 50 000.

In [17]:
df2 = df.drop(labels = [57702],axis = 0)
fig = px.histogram(df2,
                   x='sum_gamerounds',
                   color='version',
                   title='Среднее распределение прохождения уровней в игре',
                   marginal='box',
                   nbins=100,
                   barmode='overlay')

fig.show()


In [15]:
continious_result(control, treatment, 'sum_gamerounds')


100%|██████████| 10000/10000 [01:01<00:00, 163.34it/s]


effect_size     alpha      beta               CI  difference
sum_gamerounds    -0.005915  0.381339  0.856725  [-1.037, 4.096]    1.155883

Доверительный интервал включает 0, **Нет стат значимых различий.**

### Бакетирование.
--------------------------------------
разбивает данные на более управляемые части (сегменты или бакеты), чтобы ускорить последовательные чтения данных для последующих заданий. В один бакет попадают строчки таблицы, у которых совпадает значение хэш-функции, вычисленное по определенной колонке.

Способ привести распределение к нормальному и применить, например, ttest.
Когда чего применяем:

- сохранить информацию о дисперсии и среднем в выборке до трансформации.
- привести к нормальному распределению.


In [18]:
# Bucketket

for _ in range(100, 1001):
    if df.shape[0] % _ == 0:
        print(_)

911


In [20]:
n_buckets = 911
data = (df
        .sample(n=df.shape[0], replace=False)
        .reset_index(drop=True)
        .assign(bucket=list(range(n_buckets)) * int(df.shape[0] / n_buckets)))

df.head()

userid  version  sum_gamerounds  retention_1  retention_7
0     116        0               3        False        False
1     337        0              38         True        False
2     377        1             165         True        False
3     483        1               1        False        False
4     488        1             179         True         True

In [21]:
bucketed_data = data.groupby(['version', 'bucket'])['sum_gamerounds'].agg(
    mu=np.mean, std=np.std).reset_index()
bucketed_data


version  bucket         mu         std
0           0       0  67.368421  119.994141
1           0       1  43.456522   84.859022
2           0       2  53.791667   76.814216
3           0       3  54.777778  101.397344
4           0       4  36.113208   65.355142
...       ...     ...        ...         ...
1817        1     906  57.875000  119.941941
1818        1     907  45.800000   88.429841
1819        1     908  34.340000   47.999409
1820        1     909  70.867925  144.122549
1821        1     910  72.422222  105.015473

[1822 rows x 4 columns]

In [22]:
# Сравним исходное выборочное среднее и среднее бакетных средних
round(np.mean(data["sum_gamerounds"]), 5), round(
    np.mean(bucketed_data["mu"]), 5)

(51.87246, 51.81085)

In [23]:
round(np.std(data["sum_gamerounds"]), 5), round(
    np.mean(bucketed_data["std"]), 5)

(195.04978, 96.88851)

In [25]:
control_bucket = bucketed_data[bucketed_data.version == 0]
treatment_bucket = bucketed_data[bucketed_data.version == 1]
continious_result(control_bucket, treatment_bucket, 'mu', n_iters=100000)

100%|██████████| 100000/100000 [01:14<00:00, 1336.62it/s]


effect_size     alpha      beta              CI  difference
mu     -0.04006  0.392596  0.863072  [-1.007, 3.92]    1.087954

In [26]:
#Метрика retention_1
fig = px.histogram(data, x="retention_1",
                   color='version', barmode='group',
                   height=400)
fig.show()

In [27]:
proportion_result(control, treatment, 'retention_1')

100%|██████████| 10000/10000 [00:54<00:00, 181.97it/s]


effect_size     alpha      beta               CI  difference
retention_1    -0.003823  0.577181  0.911819  [-0.009, 0.005]   -0.001895

Доверительный интервал включает 0, **Нет стат значимых различий.**

In [28]:
#Метрика retention_7
fig = px.histogram(data, x="retention_7",
                   color='version', barmode='group',
                   height=500)
fig.show()


In [29]:
proportion_result(control, treatment, 'retention_7')

100%|██████████| 10000/10000 [00:47<00:00, 210.45it/s]


effect_size     alpha      beta           CI  difference
retention_7     0.012776  0.051481  0.519844  [0.0, 0.01]    0.005031

В группах **есть** статистически значимые различия, интервал включает 0, но альфа равно 5% и бетта не высокая . По этой метрике можно анализировать.

**Вывод**: поскольку для всех трех метрик alpha и beta большие, а доверительный интервал включает 0 можно сделать вывод об **отсутствиии** статистически значимых различий. 

Гипотеза **не подтвердилась** и менеджеру следует придумать что-то другое.